In [1]:
import os
import shutil
import exifread
import timm
import torch
import torchvision.transforms as transforms
import subprocess

from PIL import Image
from datetime import datetime
from collections import defaultdict
from pillow_heif import register_heif_opener
#    from mutagen import File



In [2]:
# Define paths
SOURCE_DIR = "/Volumes/NFP4TBSSD/PHOTOS_ORGANIZE"
DEST_DIR = "/Volumes/NFP4TBSSD/zz_organized_photos"

In [3]:

# Load a pre-trained image classification model (e.g., timm's resnet50)
model = timm.create_model("resnet50", pretrained=True)
model.eval()

# ImageNet labels for class names

#TODO: refactor the image labels
#LABELS_PATH = "https://raw.githubusercontent.com/pytorch/hub/master/imagenet_classes.txt"
LABELS_PATH = "../data/imagenet_classes.txt"
LABELS = [line.strip() for line in open("imagenet_classes.txt")] if os.path.exists("imagenet_classes.txt") else []


In [4]:
# Image transformation
transform = transforms.Compose([
    transforms.Resize((224, 224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225]),
])

In [5]:

register_heif_opener()  # Enable HEIC support for PIL

def get_image_metadata(image_path):
    """Extract date taken from image metadata"""
    try:
        if image_path.lower().endswith(".heic"):
            image = Image.open(image_path)
            exif_data = image.info.get("exif", None)
            if exif_data:
                return datetime.strptime(exif_data.get(36867), "%Y:%m:%d %H:%M:%S")
        else:
            with open(image_path, 'rb') as f:
                tags = exifread.process_file(f)
            date_tag = tags.get('EXIF DateTimeOriginal') or tags.get('Image DateTime')
            if date_tag:
                return datetime.strptime(str(date_tag), "%Y:%m:%d %H:%M:%S")
    except Exception as e:
        print(f"Error reading metadata for {image_path}: {e}")
    return None

In [6]:
def get_video_metadata(video_path):
    """Extract creation date from video metadata using ffmpeg"""
    try:
        cmd = ["ffprobe", "-v", "error", "-select_streams", "v:0", "-show_entries", "format_tags=creation_time", "-of", "default=noprint_wrappers=1:nokey=1", video_path]
        result = subprocess.run(cmd, stdout=subprocess.PIPE, stderr=subprocess.PIPE, text=True)
        if result.stdout:
            return datetime.strptime(result.stdout.strip(), "%Y-%m-%dT%H:%M:%S.%fZ")
    except Exception:
        pass
    return None

In [7]:
def classify_image(image_path):
    """Classify an image and return the top label."""
    if not LABELS:
        return "Unknown"
    image = Image.open(image_path).convert("RGB")
    image = transform(image).unsqueeze(0)
    with torch.no_grad():
        outputs = model(image)
    _, predicted = torch.max(outputs, 1)
    return LABELS[predicted.item()]

In [8]:

def organize_files():
    """Recursively organize files from source to destination"""
    for root, _, files in os.walk(SOURCE_DIR):
        for file in files:
            file_path = os.path.join(root, file)
            file_ext = file.lower().split('.')[-1]
            
            # Get metadata
            date_taken = None
            event_name = None
            if file_ext in ['jpg', 'jpeg', 'png', 'tiff', 'gif', 'bmp', 'webp']:
                try:
                    date_taken = get_image_metadata(file_path)
                except Exception:
                    print(f"Skipping file {file_path}: Unsupported metadata format.")
                    date_taken = None  # Fallback to modification date later
                    
                event_name = classify_image(file_path) if not date_taken else None
            elif file_ext in ['heic', 'heif']:
                # For HEIC files, we can use pyheif or similar library to extract metadata...
                date_taken = get_image_metadata(file_path)
                event_name = classify_image(file_path) if not date_taken else None
            #elif file_ext in ['mp3', 'wav', 'flac']:
            #    # For audio files, we can use a library like mutagen to extract metadata
            #    from mutagen import File
            #    audio = File(file_path)
            #    date_taken = datetime.fromtimestamp(audio.info.pprint().get('TDRL', None))
            elif file_ext in ['mp4', 'mov', 'avi', 'mkv', 'wmv']:
                date_taken = get_video_metadata(file_path)
            
            # Fallback date if metadata is missing
            if not date_taken:
                date_taken = datetime.fromtimestamp(os.path.getmtime(file_path))
            
            # Format destination path
            date_str = date_taken.strftime("%Y/%m-%d")
            dest_folder = os.path.join(DEST_DIR, date_str + ("_" + event_name if event_name else ""))
            os.makedirs(dest_folder, exist_ok=True)
            
            # Move file
            shutil.copy(file_path, os.path.join(dest_folder, file))
            print(f"Copied {file_path} -> {dest_folder}")

In [9]:
organize_files()

Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/.DS_Store -> /Volumes/NFP4TBSSD/zz_organized_photos/2025/03-27
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/250220 passe Nuno.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2025/02-20
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/desktop - 1.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2024/10-01
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/.DS_Store -> /Volumes/NFP4TBSSD/zz_organized_photos/2025/03-27
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/07-30_Unknown/66466_10152113141964358_1682040746_n.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/07-30_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/10-26/ap 004.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/10-26
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/10-26/ap 005.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/10-26
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/08-14_Unknown/tree.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/08-14_Unknown
Copied /Volumes/NFP4TBSSD/P

PNG file does not have exif data.


Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-06/ap 017.MOV -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-06
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-06/ap 043.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-06
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-06/ap 042.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-06
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-30/ap 104.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-30
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-12/ap 089.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-12
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-12/ap 088.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-12
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-12/ap 085.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-12
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-12/ap 084.JPG -> /Volumes/NFP4TBSSD/zz_organized_photos/2013/12-12
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2013/12-12/ap 079.JPG 

PNG file does not have exif data.


Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/8AE0275C-2DCF-46E0-92F0-11B1B97A7C76_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/45D4D215-8C78-445F-B741-9C9E56EB8566_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/BBF97197-0913-4815-98E6-90E14352F5C5_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/B5C344DC-1316-4EF9-B428-3C7050F6AB83_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/90C99635-06DA-40DA-9342-999A7552C15E_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/911D4C8E-1136-4E6F-80DB-838F83FDD449_1_105_c.jpeg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-13
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/2014/11-13/76AF9DD2-2E

...

Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/abbreviation-wallpaper-2560x1600.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/branched_out-wallpaper-3840x2160.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/your_life_is_loading-wallpaper-1920x1080.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/positive_thoughts-wallpaper-2880x1800.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/07-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/desktop_water-wallpaper-3200x2400.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/rules-wallpaper-1920x1080.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/07-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/black_9-wallpaper-1920x1080.jpg -> /Volum

PNG file does not have exif data.


Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/rise_of_the_tomb_raider_lara_croft-wallpaper-2560x1440.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/WarrenKeelan_Undulate.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2016/05-03_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/think_different-wallpaper-1600x900.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/believe_4-wallpaper-2560x1440.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/07-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/quote-wallpaper_22.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2016/02-26_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/fall_5-wallpaper-3840x2160.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/grimm-4.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015

PNG file does not have exif data.
PNG file does not have exif data.


Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/be_different_2-wallpaper-2560x1440.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/carreau-1.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2016/05-03_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/apple_light-wallpaper-2048x1152.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/colorful_apple_2-wallpaper-2560x1440.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2014/11-25_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/Untitled23.png -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/02-19_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/happiness_can_be_found-wallpaper-2560x1440.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/07-07_Unknown
Copied /Volumes/NFP4TBSSD/PHOTOS_ORGANIZE/Desktop 3/art_32-wallpaper-1920x1080.jpg -> /Volumes/NFP4TBSSD/zz_organized_photos/2015/